# Imports

In [1]:
from pystock.portfolio import Portfolio, Stock
from pystock.fff import FamaFrenchFactors
from frontier import EfficientFrontier
import os
import plotly.io as pio

pio.renderers.default = "notebook"
pio.templates.default = "plotly_dark"

# How to use `frontier`

There are a few steps involved:
1. Create a `Portfolio`
2. Make sure that the data of stocks in the `Portfolio` is loaded 
3. (Optional) You also need to calculate FFF parameters if you want to use FFF3 or FFF5 models.
4. That's all!

## Creating a `Portfolio`

In [2]:
stock_dir = "../../Data/Stocks/nasdaq200"
index_dir = "../../Data/Indices"

In [3]:
apple = Stock(directory=os.path.join(stock_dir, "AAPL.csv"), name="Apple")
google = Stock(directory=os.path.join(stock_dir, "GOOG.csv"), name="Google")
tesla = Stock(directory=os.path.join(stock_dir, "TSLA.csv"), name="Tesla")
microsoft = Stock(directory=os.path.join(stock_dir, "MSFT.csv"), name="Microsoft")

In [4]:
stocks = [apple, google, tesla, microsoft]
benchmark_dir = os.path.join(index_dir, "GSPC.csv")
p = Portfolio(benchmark_dir=benchmark_dir, benchmark_name="S&P 500")
p

Portfolio(S&P 500,[])

In [5]:
start_date = "2012-01-01"
end_date = "2022-12-01"
frequency = "M"
p.add_stocks(stocks, load_data=True, start_date=start_date, end_date=end_date, frequency=frequency, columns=["Close"], rename_cols=["Close"])
p

Portfolio(S&P 500,['Apple', 'Google', 'Tesla', 'Microsoft'])

In [6]:
for stock, name in p:
    print(stock.loaded, name)

False S&P 500
True Apple
True Google
True Tesla
True Microsoft


Now load the index

In [7]:
p.load_benchmark(start_date=start_date, end_date=end_date, frequency=frequency, columns=["Close"], rename_cols=["Close"])

In [8]:
for stock, name in p:
    print(stock.loaded, name)

True S&P 500
True Apple
True Google
True Tesla
True Microsoft


In [9]:
ef = EfficientFrontier(portfolio=p)

Adding portfolio...
Portfolio Summary
*****************

Portfolio with benchmark S&P 500 and stocks ['Apple', 'Google', 'Tesla', 'Microsoft']
Here are the summary of stocks in the portfolio
+----+-----------+-----------------------+----------------------+------------+----------+----------+
|    | Stock     |   Monthly_Mean_Return |   Monthly_Return_STD |      Alpha |     Beta |   Weight |
|----+-----------+-----------------------+----------------------+------------+----------+----------|
|  0 | Apple     |             0.0203446 |            0.0810776 | 0.008545   | 1.22705  |     0.25 |
|  1 | Google    |             0.0171436 |            0.0645638 | 0.00711404 | 1.04298  |     0.25 |
|  2 | Tesla     |             0.0502608 |            0.182803  | 0.0336704  | 1.72526  |     0.25 |
|  3 | Microsoft |             0.0202463 |            0.060776  | 0.010973   | 0.964346 |     0.25 |
+----+-----------+-----------------------+----------------------+------------+----------+----------+
T

In [10]:
fig = ef.plot_frontier(short=True, model="capm")

In [11]:
fig = ef.plot_frontier(short=True, model="sim")

## Using the FFF Models

First, download the FFF params as we don't have this data in our direcory.

In [12]:
ff = FamaFrenchFactors()

ff.download(frequency=frequency, factors=5, directory=".")

File already exists. Use load() to load the file. Or set overwrite=True to overwrite the file.


Now, use `Portfolio.calculate_fff_params` to calculate the params using the data you just downloaded.

In [13]:
p.calculate_fff_params(factors=5, frequency=frequency, directory=".")

Done. Here are the parameters
+-------------+-------------+------------+-------------+
|       Apple |      Google |      Tesla |   Microsoft |
|-------------+-------------+------------+-------------|
|  0.00551378 |  0.00699103 |  0.0341999 |  0.00970946 |
|  1.19761    |  1.01023    |  1.87135   |  0.994033   |
| -0.25864    | -0.572982   | -0.379263  | -0.776582   |
| -0.51356    |  0.199086   | -0.610234  |  0.0184878  |
|  0.75083    | -0.107732   | -1.45574   | -0.103125   |
| -0.181558   | -0.867854   | -0.497976  | -0.548657   |
|  1          |  1          |  1         |  1          |
+-------------+-------------+------------+-------------+


Great! Now you are ready.

In [14]:
fig = ef.plot_frontier(short=True, model="fff3")

In [15]:
fig = ef.plot_frontier(short=True, model="fff5")